In [1]:
import tensorflow as tf
import os
import numpy as np
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from keras.models import Model
from keras.applications.vgg19 import VGG19 , preprocess_input
from keras.utils import load_img, img_to_array
from zipfile import ZipFile 
from tqdm import tqdm
import re
import pickle

2024-06-14 09:05:09.912885: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-06-14 09:05:10.585244: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-06-14 09:05:12.320925: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
import json #to create dataset metadata json file

# Extract train2014.zip

In [3]:
dataPath = "data/train/train2014.zip"

In [4]:
# # Extract validate image
# with ZipFile(dataPath, 'r') as zip: 
#     # printing all the contents of the zip file 
#     zip.printdir() 
  
#     # extracting all the files 
#     print('Extracting all the files now...') 
#     zip.extractall("data/train") 
#     print('Done!') 

File Name                                             Modified             Size
train2014/                                     2014-08-16 02:08:28            0
train2014/COCO_train2014_000000270070.jpg      2014-08-16 00:53:00       232932
train2014/COCO_train2014_000000101772.jpg      2014-08-16 01:21:42       196204
train2014/COCO_train2014_000000359320.jpg      2014-08-16 00:41:00       127659
train2014/COCO_train2014_000000486482.jpg      2014-08-16 02:04:00       215507
train2014/COCO_train2014_000000116155.jpg      2014-08-16 01:54:12       263198
train2014/COCO_train2014_000000082143.jpg      2014-08-16 01:36:14       135157
train2014/COCO_train2014_000000242307.jpg      2014-08-16 01:29:00       129207
train2014/COCO_train2014_000000510484.jpg      2014-08-16 00:45:08       132713
train2014/COCO_train2014_000000339597.jpg      2014-08-16 01:49:34       113685
train2014/COCO_train2014_000000366396.jpg      2014-08-16 01:35:26        64681
train2014/COCO_train2014_000000363942.jp

# initialize a generator for the validation images

In [ ]:
# Define paths to dataset and output files
data_dir = "data/train"
output_dir = "data/train/extract"
image_dir = os.path.join(data_dir)
output_file = os.path.join(output_dir, "val_features.npy")

# Define a data generator to preprocess the images
target_size = (224, 224)
datagen = ImageDataGenerator(preprocessing_function=preprocess_input)
generator = datagen.flow_from_directory(
    image_dir,
    target_size=target_size,
    batch_size=32,
    class_mode=None,
    shuffle=False
)

Found 82783 images belonging to 4 classes.


In [ ]:
# Create an VGG19 model to extract image features
base_model = VGG19(weights='imagenet')

2024-06-14 01:07:17.063418: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-06-14 01:07:17.160855: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2251] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


In [ ]:
model = Model(inputs=base_model.input, outputs=base_model.get_layer('flatten').output)

In [ ]:
# Extract image features for each image in the training set
train_features = []
for i in tqdm(range(len(generator))):
    batch = next(generator)
    features = model.predict_on_batch(batch)
    train_features.append(features)

# model.compile(optimizer='adam',
#               loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True))

# epochs = 320
# train_features = model.fit(
#     generator,
#     epochs=epochs
# )


# Concatenate and reshape the extracted features into a numpy array
train_features = np.concatenate(train_features)
train_features = train_features.reshape((len(generator.filenames), -1))

# Save the extracted features to a numpy file
np.save(output_file, train_features)

 47%|████▋     | 1225/2587 [1:32:01<1:55:46,  5.10s/it]

# save features with IDs in a dictionary in a pkl file

In [ ]:
# add ids to features
img_ids = np.array([int(re.search("[0-9][0-9][0-9][0-9][0-9]+", gen).group()) for gen in generator.filenames])
image_features = {}
for i in range(len(img_ids)):
    image_features[img_ids[i]]= train_features[i]

In [ ]:
# save dictionary to train_image_features.pkl file
with open('train_image_features.pkl', 'wb') as fp:
    pickle.dump(image_features, fp)
    print('dictionary saved successfully to file')

dictionary saved successfully to file
